In [1]:
from textwrap import dedent

from agno.agent import Agent
from agno.models.openai import OpenAILike
from agno.exceptions import StopAgentRun
from agno.tools import tool,FunctionCall
from agno.tools.function import UserInputField
from agno.utils import pprint

from dotenv import load_dotenv 

from typing import Iterator,List

from rich.console import Console
from rich.prompt import Prompt

import httpx
import os
import json
load_dotenv()

True

**User Control Flows(Human in loop)**

In [2]:
# This is the console instance used by the print_response method
# We can use this to stop and restart the live display and ask for user confirmation
console = Console()


def pre_hook(fc: FunctionCall):
    # Get the live display instance from the console
    live = console._live

    # Stop the live display temporarily so we can ask for user confirmation
    live.stop()  # type: ignore

    # Ask for confirmation
    console.print(f"\nAbout to run [bold blue]{fc.function.name}[/]")
    message = (
        Prompt.ask("Do you want to continue?", choices=["y", "n"], default="y")
        .strip()
        .lower()
    )

    # Restart the live display
    live.start()  # type: ignore

    # If the user does not want to continue, raise a StopExecution exception
    if message != "y":
        raise StopAgentRun(
            "Tool call cancelled by user",  
            agent_message="Stopping execution as permission was not granted.",
        )


@tool(pre_hook=pre_hook)
def get_top_hackernews_stories(num_stories: int) -> Iterator[str]:
    """Fetch top stories from Hacker News after user confirmation.

    Args:
        num_stories (int): Number of stories to retrieve

    Returns:
        str: JSON string containing story details
    """
    # Fetch top story IDs
    response = httpx.get("https://hacker-news.firebaseio.com/v0/topstories.json")
    story_ids = response.json()

    # Yield story details
    for story_id in story_ids[:num_stories]:
        story_response = httpx.get(
            f"https://hacker-news.firebaseio.com/v0/item/{story_id}.json"
        )
        story = story_response.json()
        if "text" in story:
            story.pop("text", None)
        yield json.dumps(story)


# Initialize the agent with a tech-savvy personality and clear instructions
agent = Agent(
    model=OpenAILike(id="qwen3-30b-a3b", 
                    api_key=os.getenv("BAILIAN_API_KEY"), 
                    base_url=os.getenv("BAILIAN_API_BASE_URL"),
                    request_params={"extra_body": {"enable_thinking": False}},),
    description="A Tech News Assistant that fetches and summarizes Hacker News stories",
    instructions=dedent("""\
        You are an enthusiastic Tech Reporter

        Your responsibilities:
        - Present Hacker News stories in an engaging and informative way
        - Provide clear summaries of the information you gather

        Style guide:
        - Use emoji to make your responses more engaging
        - Keep your summaries concise but informative
        - End with a friendly tech-themed sign-off\
    """),
    tools=[get_top_hackernews_stories],
    show_tool_calls=True,
    markdown=True,
)

# Example questions to try:
# - "What are the top 3 HN stories right now?"
# - "Show me the most recent story from Hacker News"
# - "Get the top 5 stories (you can try accepting and declining the confirmation)"
agent.print_response(
    "What are the top 2 hackernews stories?", stream=True, console=console
)

Output()

About to run get_top_hackernews_stories

Do you want to continue? [y/n] (y):

In [ ]:
# You can either specify the user_input_fields leave empty for all fields to be provided by the user
@tool(requires_user_input=True, user_input_fields=["subject", "to_address"])
def send_email(subject: str, body: str, to_address: str) -> str:
    """
    Send an email.

    Args:
        subject (str): The subject of the email.
        body (str): The body of the email.
        to_address (str): The address to send the email to.
    """
    return f"Sent email to {to_address} with subject {subject} and body {body}"

agent = Agent(
    model=OpenAILike(id="qwen3-32b", 
                    api_key=os.getenv("BAILIAN_API_KEY"), 
                    base_url=os.getenv("BAILIAN_API_BASE_URL"),
                    request_params={"extra_body": {"enable_thinking": False}},),
    tools=[send_email],
    show_tool_calls=True,
    markdown=True,
)

agent.run("Send an email with the body 'Hello, world!'")
if agent.is_paused and agent.run_response:
    for tool in agent.run_response.tools_requiring_user_input:
        if tool.user_input_schema:
            input_schema: List[UserInputField] = tool.user_input_schema

        for field in input_schema:
            # Display field information to the user
            print(f"\nField: {field.name}")
            print(f"Description: {field.description}")
            print(f"Type: {field.field_type}")

            # Get user input
            if field.value is None:
                user_value = input(f"Please enter a value for {field.name}: ")
                # Update the field value
                field.value = user_value
            else:
                print(f"Value: {field.value}")

    run_response = agent.continue_run()
    pprint.pprint_run_response(run_response)


Field: subject
Description: The subject of the email.
Type: <class 'str'>

Field: body
Description: The body of the email.
Type: <class 'str'>
Value: Hello, world!

Field: to_address
Description: The address to send the email to.
Type: <class 'str'>


╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╮
│ The email with the body "Hello, world!" has been successfully sent. Let me know if there's anything else I can  │
│ assist you with!                                                                                                │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯